### Imports for sections I - III

In [72]:
import io
import os
import re
import random
import requests
from zipfile import ZipFile
import apache_beam as beam
from apache_beam.runners.interactive.interactive_runner import InteractiveRunner
import apache_beam.runners.interactive.interactive_beam as ib
from google.cloud import storage

# I. The Dataset: SSA (USA) Baby Names 

* https://www.ssa.gov/oact/babynames/limits.html
* https://www.ssa.gov/oact/babynames/background.html

All names are from Social Security card applications for births that occurred in the United States after 1879. Note that many people born before 1937 never applied for a Social Security card, so their names are not included in our data. For others who did apply, our records may not show the place of birth, and again their names are not included in our data.

The format of the data in the three file collections is described in a "readme" file contained in the respective zip files.

* National data: https://www.ssa.gov/oact/babynames/names.zip
* State-specific adata: https://www.ssa.gov/oact/babynames/state/namesbystate.zip
* Territory-specific data: https://www.ssa.gov/oact/babynames/territory/namesbyterritory.zip

## I.a  Prestaging

Google Cloud's Storage client is easy and accessible.  Before we stage our files directly from the SSA's website, we'll collect and pre-process all of the information we need (such as URLs, file names, and folders).  

One of the best parts of the client library is that once a bucket has been represented as a python object, we can easily re-use it within the rest of our workflow.  

In [191]:
usa_names_bucket_name = "yaquino-x532"  # Must be globally unique!
usa_names_client = storage.Client()
usa_names_url = 'https://www.ssa.gov/oact/babynames/names.zip'
usa_names_path, usa_names_file = os.path.split(usa_names_url)
usa_names_bucket = usa_names_client.create_bucket(usa_names_bucket_name) # returns the bucket
usa_names_bucket
usa_names_folder = 'usa_names'

print('URL:', usa_names_url)
print('URL path:', usa_names_path)
print('File:', usa_names_file)
print('Bucket:', usa_names_bucket.name)
print('Folder:', usa_names_folder)

URL: https://www.ssa.gov/oact/babynames/names.zip
URL path: https://www.ssa.gov/oact/babynames
File: names.zip
Bucket: yaquino-x532
Folder: usa_names


## I.b  Staging

With our information ready for staging, we're going to process the data in-memory (and without writing it to the local disk) and stage directly to Google Cloud Storage.  The dataset is composed of 140 text files that are comma delimited lines representing a name, a count, and the recorded gender - we're going to inject the year as a feature into each row before we upload the files to GCS.  

The Source data is compressed into a zip archive.  The data will be extracted in memory, the files will be iterated over, manipulated, and then staged on to GCS.   

In [192]:
with requests.get(usa_names_url) as resp:
    resp_bytes = resp.content
    archive_stream = io.BytesIO(resp_bytes)
    
    with ZipFile(archive_stream) as archive:
        files = archive.namelist()
        for file in files:
            if not file.endswith('.txt'):
                continue
            year = file[3:7]
            file_stream = io.BytesIO()
            with archive.open(file) as text:
                for line in text:
                    updated_line = line[:-2] + bytes(f',{year}\r\n'.encode())
                    file_stream.write(updated_line)
            usa_names_blob_name = os.path.join(usa_names_folder, file)
            usa_names_blob = usa_names_bucket.blob(usa_names_blob_name)
            usa_names_blob.upload_from_string(file_stream.getvalue())

## I.c Checking the Work

The files have been staged to GCP.  Let's sample a handful of files to make sure the upload went as planned.  

In [175]:
files = [blob.name for blob in usa_names_bucket.list_blobs() if blob.name.endswith('.txt')]
samples = random.sample(files, 3)
for file in samples:
    usa_names_blob = usa_names_bucket.blob(file)
    usa_names_data = usa_names_blob.download_as_string().decode()
    print('File:', file)
    print('link:', usa_names_blob.public_url)
    for index, line in enumerate(usa_names_data.split()):
        if index >= 5:
            break
        print('----', 'Sample row:', line) 

File: usa_names/yob1969.txt
link: https://storage.googleapis.com/end-to-end-analysis-demo-i/usa_names/yob1969.txt
---- Sample row: Lisa,F,45029,1969
---- Sample row: Michelle,F,34320,1969
---- Sample row: Jennifer,F,33702,1969
---- Sample row: Kimberly,F,33079,1969
---- Sample row: Melissa,F,23022,1969
File: usa_names/yob1889.txt
link: https://storage.googleapis.com/end-to-end-analysis-demo-i/usa_names/yob1889.txt
---- Sample row: Mary,F,11648,1889
---- Sample row: Anna,F,5062,1889
---- Sample row: Elizabeth,F,3058,1889
---- Sample row: Margaret,F,2917,1889
---- Sample row: Emma,F,2884,1889
File: usa_names/yob2009.txt
link: https://storage.googleapis.com/end-to-end-analysis-demo-i/usa_names/yob2009.txt
---- Sample row: Isabella,F,22311,2009
---- Sample row: Emma,F,17900,2009
---- Sample row: Olivia,F,17437,2009
---- Sample row: Sophia,F,16948,2009
---- Sample row: Ava,F,15873,2009


# II.  Serverless ETL with Cloud DataFlow

Cloud Dataflow is a managed service for executing a wide variety of data processing patterns.  It is a serverless computation engine for processing ETL, jobs are written in open source Apache Beam.  Dataflow excels at embarrassingly parallel processing.  

## II.a Light Intro to Cloud Dataflow and Apache Beam

Beam is the third spiritual successor to MapReduce, its open source, it addresses unifying the semantics of batch and streaming, and its designed to be portable.  

Apache Beam’s SDK is great for teams - it provides a level of standardization in ETL that most programming languages can’t.  Instead of allowing your team to ‘roll-their-own’, Beam is batteries included so your team can easily perform processing and preprocessing.  

A basic example of squaring a given number is provided below 

In [183]:
nums = [1, 2, 3, 4, 5]

with beam.Pipeline(InteractiveRunner()) as p: 
    squares = (
        p
        | beam.Create(nums)  # Creates a 'pcollection' based of a python collection
        | beam.Map(lambda x: x**2)
        | beam.Map(print) # Applies the print function to each element
    )

1
4
9
16
25


## II.b Interactive Beam


Using the Apache Beam interactive runner with JupyterLab notebooks lets you iteratively develop pipelines, inspect your pipeline graph, and parse individual PCollections in a read-eval-print-loop (REPL) workflow. 

Replacing the `DirectRunner` with the  `InteractiveRunner` is trivial. `InteractiveRunner` has built-in capabilities like showing the pipeline graph or seeing the output without the need of `print`. 

Getting back to our USA Names example, let's start small with a single file, we're going to process 140 files in serverlessly in parallel.  Each file is composed of rows, we need to split the rows into elements and convert them into JSON like key-value pairs.  The general workflow looks like this.

(str)  `Dorothy,F,39999,1924` --> split on comma

(list) `['Dorothy, 'F', '39999', '1924']` --> map to key-values

(dict) `{'Name': 'Dorothy', 'Sex': 'F', 'Count': '39999', 'Year': '1924'}` --> write to BigQuery


In [162]:
with beam.Pipeline(InteractiveRunner()) as p: 
    
    columns = ('name', 'gender', 'count', 'year')
    
    usa_names_pipeline = (
        p
        | 'Read from memory ' >> beam.Create([usa_names_data])  # left over from last iteration of sampling
        | 'Flat map to lines ' >> beam.FlatMap(lambda big_str: big_str.split('\r\n')) # split on return-new line feed 
        | 'Process each line ' >> beam.Map(lambda line: line.split(','))
        | 'Map to keys ' >> beam.Map(lambda elem: {key: value for key, value in zip(columns, elem)})
    )
    
    ib.show_graph(p)
    ib.show(usa_names_pipeline)


While Apache Beam is batteries included, the SDK provides a framework for you to create composite transforms which you can use and re-use in other pipelines.  Separate transforms can be managed in a centralized, curated package to offer more consistent results across teams.

In [129]:
# Composite Transform, user provided input.
class ListFilesFromGcs(beam.PTransform):
    
    def __init__(self, file_pattern):
        self.file_pattern = file_pattern
        
    def expand(self, pcoll):
        file_paths = beam.io.gcp.gcsio.GcsIO().list_prefix(self.file_pattern)
        return (
            pcoll
            | beam.Create(file_paths)
            | beam.Map(lambda element: element[0]) # dicts are broken down to items by Create.
        )
    

# Custom Function , side-input pattern
class SplitLinesAndConvertToRecords(beam.DoFn):
    
    def process(self, element, columns):
        values = element.split(',')
        record = {key: value for key, value in zip(columns, values)}
        yield record
        
    
with beam.Pipeline(InteractiveRunner()) as p: 
    
    columns = ('name', 'gender', 'count', 'year')
    
    usa_names_files = (
        p
        | 'Generate files list from GCS' >> ListFilesFromGcs(file_pattern)
    )
    
    usa_names_pipeline = (
        usa_names_files
        | 'Read all files from the list' >> beam.io.ReadAllFromText()
        | 'Split and convert rows to records' >> beam.ParDo(SplitLinesAndConvertToRecords(), columns=columns)
    )
    
    ib.show(usa_names_pipeline)
    ib.show_graph(p)

## II.c Production 

We're ready to produce data.  To 'run' this pipeline, need to switch the `InteractiveRunner` with the `DataflowRunner` and configure it's options which are primarily location related.  Since we're using globally scoped imports, we'll run this code in a separate notebook / interpreter environment - the Dataflow Runner pickles (serializes) up code and environment and then runs it on GCP's Dataflow Runner so it always makes sense to start with a clean environment. 

The final pipeline looks like this:

In [184]:
%%writefile usa_names_pipeline.py
# AI platform notebook cell magic to write the content directly to a file 

import os
import apache_beam as beam

# # Custom Transforms and Do Functions. 
# Composite Transform, user provided input.
class ListFilesFromGcs(beam.PTransform):
    
    def __init__(self, file_pattern):
        self.file_pattern = file_pattern
        
    def expand(self, pcoll):
        file_paths = beam.io.gcp.gcsio.GcsIO().list_prefix(self.file_pattern)
        return (
            pcoll
            | beam.Create(file_paths)
            | beam.Map(lambda element: element[0]) # dicts are broken down to items by Create.
        )
    

# Custom Function , side-input pattern
class SplitLinesAndConvertToRecords(beam.DoFn):
    
    def process(self, element, columns):
        values = element.split(',')
        record = {key: value for key, value in zip(columns, values)}
        yield record

        
# # Options, arguments, and parameters. 
write_to_bigquery_params = dict(
    table='fedciv-usgs-experimental:testing.ssa_baby_names_iii', 
    schema='SCHEMA_AUTODETECT',
    create_disposition='CREATE_IF_NEEDED',
    write_disposition='WRITE_TRUNCATE', 
    custom_gcs_temp_location='gs://fedciv-usgs-experimental/end-to-end-analysis/staging'
)

pipeline_options_args = {
    'region': 'us-east1',
    'runner': 'DataflowRunner',
    'project': 'fedciv-usgs-experimental',
    'temp_location': 'gs://fedciv-usgs-experimental/end-to-end-analysis/staging'
}

pipeline_options = beam.options.pipeline_options.PipelineOptions.from_dictionary(pipeline_options_args)
# We use the save_main_session option because one or more DoFn's in this
# workflow rely on global context (e.g., a module imported at module level).
pipeline_options.view_as(beam.options.pipeline_options.SetupOptions).save_main_session = True


with beam.Pipeline(options=pipeline_options) as p: 
    
    file_pattern = 'gs://end-to-end-analysis-demo-i/usa_names/yob'
    columns = ('name', 'gender', 'count', 'year')
    
    usa_names_files = (
        p
        | 'Generate files list from GCS' >> ListFilesFromGcs(file_pattern)
    )
    
    usa_names_pipeline = (
        usa_names_files
        | 'Read all files from the list' >> beam.io.ReadAllFromText()
        | 'Split and convert rows to records' >> beam.ParDo(SplitLinesAndConvertToRecords(), columns=columns)
    )
    
    usa_names_pipeline | 'Write to BigQuery' >> beam.io.WriteToBigQuery(**write_to_bigquery_params)  # Dict unpacking

Overwriting usa_names_pipeline.py


In [ ]:
# Jupyter call to the terminal.  
!python3 usa_names_pipeline.py

# III. Serverless SQL ELT for EDA 

This part of the demo is conducted in the BigQuery Console.

# Imports for IV

In [139]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from ipywidgets import interact, interactive, fixed, interact_manual
import ipywidgets as widgets

# IV. Exploratory Data Analysis with Interactive Jupyter

Notebooks let us bring EDA to life with great ease.  

We were able to ELT and curate our dataset in BigQuery - but now we want to explore it back in a Notebook.  Cloud AI Platform Notebooks come with bigquery magic methods that let us easily interface with BigQuery - no need for extra libraries and coding, we can quickly query BigQuery and load data into a dataframe to continue our EDA. 

In [146]:
%%bigquery df
SELECT *
FROM `fedciv-usgs-experimental.testing.strongly_nonbinary_names_ii`

In [147]:
df = df.set_index('Year') # Indexy by year, in separate cell - not idempotent!

Notebooks come alive when interactive widgets are used. Users can visualize and control changes in the data. Learning becomes an immersive, plus fun, experience. Researchers can easily see how changing inputs to a model impacts the results.  We can use the Jupyter Interact Framework to accelerate our EDA activities.

Interact lets us define widgets such as sliders and selectors so we can dynamically work with our data in vivo.

In [145]:
sns.set_theme()
def plotter(name):
    name_df = df[df['Name'] == name]
    ax_bias = name_df['male_bias'].plot.line(figsize=(16, 12), label='Male Bias')
    ax_bias.set_ylabel('Male bias')
    ax_bias.set_ylim(-0.1, 1.1)
    ax_bias.set_xlim(1878, 2020)
    ax_bias.axhline(name_df['male_bias'].mean(), color='g', label='Mean Male Bias').set_linestyle('--')
    ax_pop = ax_bias.twinx()
    ax_pop = name_df['total_count'].plot.line(color='r', label='Total Count')
    return ax_pop.legend()

interact(plotter, name=df.Name.unique())

interactive(children=(Dropdown(description='name', options=('Addison', 'Adell', 'Adrain', 'Adrian', 'Adriel', …

<function __main__.plotter(name)>